In [1]:
import numpy as np
from scipy.io import wavfile
from scipy import signal
import matplotlib.pyplot as plt
from PyQt5.QtWidgets import *
from PyQt5.QtMultimedia import *
from PyQt5.QtMultimediaWidgets import *
from PyQt5.QtCore import QThread, Qt, pyqtSignal, pyqtSlot, QPoint
from PyQt5.QtGui import *
import sys
import os
import time
import wave
import shutil
import numpy as np
import soundfile as sf
import sounddevice as sd
import speech_recognition as sr
from scipy.io.wavfile import write
from PyQt5.QtCore import QTimer, QDateTime
import matplotlib.pyplot as plt
from datetime import datetime
from pydub import AudioSegment

C:\Users\Mihai\anaconda3\envs\am\lib\site-packages\pydub\utils.py:170: RuntimeWarning: Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work
  warn("Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work", RuntimeWarning)


In [2]:
# Clasa ferestrei principale
class MainWindow(QMainWindow):
      
    # Constructor
    def __init__(self):
        super().__init__()
        # Setare titlu fereastra
        self.setWindowTitle("Proiect AM - Stoian Mihai")
        
        # Extragere dimensiuni ecran
        self.width = QDesktopWidget().screenGeometry(-1).width()
        self.height = QDesktopWidget().screenGeometry(-1).height()
        
        # Setare dimensiuni fereastra proportional cu dimensiunile ecranului
        self.setGeometry(100, 100, 1500, 800)
        
        # Functie definita mai jos care deseneaza butoanele
        self.UiComponents() 
        
        # Afisare fereastra principala
        self.show()
        
    def UiComponents(self):
        
        ### Dimensiuni elemente ###
        w_align = int( self.width/15 )
        h_align = int( self.height/15 )
        w_btn = int( self.width/10 )
        h_btn = int( self.height/20 )
        
        self.target_words = ["restanță"]
        self.do_record = False
        self.audio_data = []
        self.user_message = ""
        
        ### Variabile ale timerului ###
        self.count = 0
        self.flag = False
        ###############################
        
        #### Intefata ###

        self.label_plot = QLabel("", self)
        self.label_plot.setGeometry(750, 100, 600, 800)

        self.label_log = QLabel(self)
        self.label_log.setText(self.user_message)
        self.label_log.setGeometry(150,275,500,500)
        self.label_log.setFont(QFont('Arial', 8))
        #Timer
      
        self.timer_label = QLabel(self)
        self.timer_label.setGeometry(1250, 80, 200, 40)
        self.timer_label.setText(str(self.count))
        self.timer_label.setFont(QFont('Arial', 15))
        
        timer = QTimer(self)
        timer.timeout.connect(self.showTime)
        timer.start(100)
        
        
        self.label_text = QLabel(" Start Audio will open the microphone and capture the audio to be processed ",self)
        self.label_text.setGeometry(150, 250, 1500, 25)
        self.label_text.setFont(QFont('Arial', 8))
        
        self.button_record = QPushButton(" Start recording ", self)
        self.button_record.setGeometry( 3*w_align, h_align, w_btn, h_btn)
        self.button_record.pressed.connect(self.record)

        self.button_stop_recording = QPushButton(" Stop recording ", self)
        self.button_stop_recording.setGeometry( 6*w_align, h_align, w_btn, h_btn)
        self.button_stop_recording.setEnabled(False)
        self.button_stop_recording.pressed.connect(self.stop_recording)

        
    ### Functii Timer ###
    
   	# method called by timer
    def showTime(self):
    	if self.flag:
    		self.count+= 1
    	text = str(self.count / 10)
    	self.timer_label.setText(text)
        
    def Start(self):
    	self.flag = True

    def Re_set(self):
    	self.flag = False
    	self.count = 0
    	self.timer_label.setText(str(self.count))
        
    ########################################

    ###########################################################
    # Functia de construire a fisierului .wav final(cenzurat) #
    ###########################################################

    def build_wav(self,audio_id):
        index = 1
        # segmentul normal
        filepath = f"Censored/segment_{index}__{audio_id}.wav"

        # segmentul de tranzitie
        filepath_T = f"Censored/T_segment_{index}__{audio_id}.wav"

        filepath_out = f"Censored/censored_file__{audio_id}.wav"
        sound_out = AudioSegment.silent(duration=0)
    
        while(os.path.exists(filepath)==True):
                # deschid segmentul 
                sound_1 = AudioSegment.from_wav(filepath)
                    # daca avem segment de tranzitie
                if(os.path.exists(filepath_T)==True):
                    # il deschid
                    sound_2 = AudioSegment.from_wav(filepath_T)
                    # fisierul unde vreau sa scriu si segment si segment de tranzitie
                    sound_out = sound_out + sound_1 + sound_2
                         
                    #altfel avem doar segment normal
                else :
                    sound_out = sound_out + sound_1
                
                # Actualizam index si locatiile unde ne asteptam sa fie fisiere
                index = index + 1
                filepath = f"Censored/segment_{index}__{audio_id}.wav"
                filepath_T = f"Censored/T_segment_{index}__{audio_id}.wav"

        sound_out.export(filepath_out, format="wav")
                    
    ########################################
    # Functia de cropare a secventei audio #
    ########################################
    
    def crop(self,audio_id, index,which_one_2_crop):
        filepath = f"Censored/segment_{index+1}"+ "__" + audio_id + ".wav"
        # citim informatiile despre fisierul audio
        with wave.open(file_path, 'rb') as wav_file:
            params = wav_file.getparams()
            sample_width = wav_file.getsampwidth()
            frames_bytes = wav_file.readframes(params.nframes)
    
        audio_data = np.frombuffer(frames_bytes, dtype=np.int16)
    
        sample_rate = params.framerate
        # pentru ca cropam o secunda si facem segment de tranzitie de 2 secunde
        # deci o secunda din fiecare segment
        frames_to_crop = 1 * sample_rate

        # daca avem first cropam primele daca avem last ultimele, deci :
        if which_one_2_crop == "first":
            cropped_audio = audio_data[frames_to_crop:]
        elif which_one_2_crop == "last":
            cropped_audio = audio_data[:-frames_to_crop]
            
        with wave.open(f"Censored/segment_{index+1}"+ "__" + audio_id + ".wav", 'wb') as output_file:
            output_file.setparams(params)
            output_file.writeframes(cropped_audio.tobytes())
            
    ##########################################
    # Functia de cenzurare a secventei audio #
    ##########################################
    
    def censor(self,audio_id,index,timestamps,is_T):
        # variabila care ne ajuta sa modificam locatia in functie de ce segment este
        if(is_T == 1):
                
                file_path = f"T_Batches/T_segment_{index + 1}__{audio_id}.wav"
                print(f" Se apeleaza pentru : T_Batches/T_segment_{index + 1}__{audio_id}.wav")
                output_fp = f"Censored/T_segment_{index + 1}__{audio_id}.wav"
        else:
                print(f" Se apeleaza pentru : Batches/segment_{index + 1}__{audio_id}.wav")
                file_path = f"Batches/segment_{index + 1}__{audio_id}.wav"
                output_fp = f"Censored/segment_{index + 1}__{audio_id}.wav"

        # fisierul cu sunetul de cenzura
        censor_file = f"censor-beep-7.wav"
        censor_sound = AudioSegment.from_wav(censor_file)
    
        original_audio = AudioSegment.from_file(file_path)


        # copiem audioul original ca sa lucram pe el
        censored_audio = original_audio[:]

        # iteram prin timestampuri
        for timestamp in timestamps:
            # covertim timestampul din s in ms
            censor_timestamp_ms = timestamp * 1000
            #print(f"Applying censor at timestamp: {censor_timestamp_ms} ms")

            # Detminam timpul de inceput si sfarsit al cenzurii
            
            start_time = max(0, censor_timestamp_ms - len(censor_sound) // 2)
            end_time = min(len(original_audio), censor_timestamp_ms + len(censor_sound) // 2)

            # determinam secventele audio de dinainte si de dupa cenzura
            audio_before_censor = original_audio[:start_time]
            audio_after_censor = original_audio[end_time:]
            
            # Contruim fisierul audio din secventele mentionate mai sus
            censored_audio = audio_before_censor + censor_sound + audio_after_censor
            
            # actualizam audioul pe care lucram, altfel se cenzureaza doar ultimul timestamp
            original_audio = censored_audio
        censored_audio.export(output_fp, format="wav")

    
    ###########################################
    # Functia de segmentare a fisierului .wav #
    ###########################################
    
    def batch(self,audio_id):
        # reconstruim filepath - ul cu ajutorul id-ului
        audio_file_path = audio_id + " recorded_audio.wav"
        print(audio_file_path)
        # Actualizam mesajul pentru utilizator cu numele fisierului
        self.user_message  = self.user_message + f"Numele fisierului audio este : {audio_file_path} \n"
        self.label_log.setText(self.user_message)

        # extragem detalii despre segment
        audio_data, sample_rate = sf.read(audio_file_path)
        # calculam cate sample-uri o sa fie in 30 de secunde
        samples_per_segment = int(sample_rate * 30)
        # aflam numarul total de segmente
        total_segments = len(audio_data) // samples_per_segment

        # pentru fiecare index
        for i in range(total_segments):
            # calculam de unde incepe, inmultim index cu cate sample-uri sunt pe segment
            start_sample = i * samples_per_segment
            # calculam unde se termina
            end_sample = start_sample + samples_per_segment
            
            # determinam segmentul din momentele de timp calculate anterior
            segment = audio_data[start_sample:end_sample]
            
            # filepath-ul unde o sa scriem fisierul
            segment_file_path = f"Batches/segment_{i + 1}"+ "__" + audio_id + ".wav"
            sf.write(segment_file_path, segment, sample_rate, 'PCM_24')

        # verificam daca au mai ramas sample-uri 
        remaining_samples = len(audio_data) % samples_per_segment
        # daca da mai facem un segment cu sample-urile ramase
        if remaining_samples > 0:
            last_segment = audio_data[-remaining_samples:]
            last_segment_file_path = f"Batches/segment_{total_segments + 1}" + "__" + audio_id +".wav"
            sf.write(last_segment_file_path, last_segment, sample_rate, 'PCM_24')
            total_segments = total_segments+1
        return total_segments

    ######################################
    # Functie creeare segmente tranzitie #
    ######################################

    def transition_segment(self, audio_id, total_segments):
        # parcurgem toate segmentele
        for i in range(1, total_segments+1):
            if i != total_segments:
                # setam filepath-urile pentru fisiere
                filepath_1_in = f"Batches/segment_{i}__{audio_id}.wav"
                filepath_2_in = f"Batches/segment_{i+1}__{audio_id}.wav"
                filepath_out = f"T_Batches/T_segment_{i}__{audio_id}.wav"
                
                # citim primul segment, luam numarul de frame-uri si creeam fisier auxiliar cu ele
                with wave.open(filepath_1_in, 'rb') as file_1:
                    frame_rate = file_1.getframerate()
                    num_frames = file_1.getnframes()
                    frames_per_1_sec = int(frame_rate * 1)
                    start_frame = max(0, num_frames - frames_per_1_sec)
                    with wave.open("aux1.wav", 'wb') as aux_1_out:
                        aux_1_out.setparams(file_1.getparams())
                        file_1.setpos(start_frame)
                        aux_1_out.writeframes(file_1.readframes(frames_per_1_sec))
                
                # citim al doilea segment, luam numarul de frame-uri si creeam fisier auxiliar cu ele
                with wave.open(filepath_2_in, 'rb') as file_2:
                    frame_rate = file_2.getframerate()
                    num_frames = file_2.getnframes()
                    frames_per_1_sec = int(frame_rate * 1)
                    with wave.open("aux2.wav", 'wb') as aux_2_out:
                        aux_2_out.setparams(file_2.getparams())
                        aux_2_out.writeframes(file_2.readframes(frames_per_1_sec))
                
                # concatenam cele 2 fisiere si obtinem fisier de tranzitie
                with wave.open("aux1.wav", 'rb') as last2, wave.open("aux2.wav",'rb') as first2:
                    with wave.open(filepath_out, 'wb') as file_out:
                        file_out.setparams(last2.getparams())
                        file_out.writeframes(last2.readframes(last2.getnframes()))
                        file_out.writeframes(first2.readframes(first2.getnframes()))
                        
                # stergem fisierele auxiliare
                os.remove("aux1.wav")
                os.remove("aux2.wav")
                

    #####################################################
    ###     Functia de calculare a timestamp-ului     ###
    #####################################################

    def get_timestamp(self,filepath,timestamp_count):
        snippet = 'identify.wav'
        source  = filepath
        timestamps=[]
        
        if(timestamp_count == 0):
            return timestamps
        
        # read the sample to look for
        rate_snippet, snippet = wavfile.read(snippet);
        
        snippet = np.array(snippet[:,0], dtype='float')
        

        # read the source
        rate, source = wavfile.read(source);
        source = np.array(source[:,0], dtype='float')
        
        # resample such that both signals are at the same sampling rate (if required)
        if rate != rate_snippet:
            num = int(np.round(rate*len(snippet)/rate_snippet))
            snippet = signal.resample(snippet, num)
            
        x_snippet = np.arange(0, snippet.size) / rate_snippet
        x_source = np.arange(0, source.size) / rate
        
        # compute the cross-correlation
        z = signal.correlate(source, snippet, mode='same')
        x_z = np.arange(0, z.size) / rate
    
        # transmitem ca parametru cate trebuie sa avem conform cu speech_recognizer
        initial_height = 3e18
        height = initial_height
        step = 5e17
        count_iter = 0
        while(True):
            timestamps=[]
            peaks = signal.find_peaks(
                z,
                height = height - step,
                distance=50000
            )
            peaks_idxs = peaks[0]
            for i, peak_idx in enumerate(peaks_idxs):
                start = (peak_idx-snippet.size/2) / rate
                center = (peak_idx) / rate
                end   = (peak_idx+snippet.size/2) / rate
                # timestampurile o sa fie in secunde
                # aici am incercat sa modific sa fie putin mai devreme fie putin mai tarziu timestamp-ul
                # in principiu cele mai bune rezultate le am obtinut lasand forma de mai jos
                timestamps.append(round(center,2))
                
            # daca am acelasi numar de timestamp-uri cu nr de word_count ma opresc
            if(len(timestamps) == timestamp_count):
                print("A reusit sa indentifice !")
                break
            # daca am mai putine inseamna ca trebuie sa maresc pazul, cand "cobor"
            elif(len(timestamps) < timestamp_count):
                height = initial_height
                step = step + (step * 1) / 100
                print("Caz nefericit, reincepem cautarea si marim pasul cu 0.5%")
                
            # altfel inseamna ca am mai multe cuvinte si am avut pasul prea mare, deci trebuie sa-l scad
            else :
                print("Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%")
                height = initial_height
                step = step - (step * 1) / 100
            count_iter = count_iter + 1
            print(f"Count iter : {count_iter}")
            if(count_iter == 25000):
                print("Nu am putut identifica timestampurile !")
        return timestamps
        
    #####################################################
    ### Functia de detectare a cuvintelor in segmente ###
    #####################################################
    
    def count_word_and_timestamps(self,audio_id, target_words,total_segments,aux):
        ### https://www.geeksforgeeks.org/python-convert-case-of-elements-in-a-list-of-strings/
        # cuvintele tina sunt puse intr-o lista pentru ca a ramas asa de la prima varianta, acum exista doar un cuvant tinta
        # care este inregistrat sub forma audio
        out = map(lambda x:x.lower(), target_words)
        target_words = list (out)
        
        word_count = []
        timestamps = []
        recognizer = sr.Recognizer()
        # variabila dupa care determinam daca functia este apelata pentru un segment de tranzitie sau unul normal
        if(aux == 1):
            for i in range(1,total_segments+1):
              # determinam filepath-u;
              file_path = f"Batches/segment_{i}__{audio_id}.wav"
              segment_timestamps = []
              segment_word_count = 0
              info = sf.info(file_path) 
              segment_duration_seconds = info.duration

              # deschidem fisierul ce trebuie prelucrat
              with sr.AudioFile(file_path) as source:
                # extrage date din fisier
                audio_data = recognizer.record(source)
                try:
                    # converteste datele in text in limba romana
                    text = recognizer.recognize_google(audio_data, language="ro-RO")  
                    # separam cuvintele si le transformam in litere mici
                    text_words = text.lower().split()

                    # pentru fiecare cuvant obtinut
                    for word in text_words:
                        if word in target_words:
                            # daca e prin cuvintele tinta incrementam
                            segment_word_count += 1
                    # apelam functia de get_timestamp pentru tot segmentul
                    segment_timestamps = self.get_timestamp(file_path,segment_word_count)
                    # adaugam la lista finala de momente de timp
                    timestamps.append(segment_timestamps)
                    # adaugam la lista finala de aparitii
                    word_count.append(segment_word_count)
                    
                ### tratare erori (nu a indentificat nici un cuvant in fisier)
                except sr.UnknownValueError:
                    print(f"Speech recognition could not understand the audio in the segment {i} ")
                    self.user_message = self.user_message + f"Speech recognition could not understand the audio in the segment {i} \n"
                    self.label_log.setText(self.user_message)
                    word_count.append(0)
                    timestamps.append([])
                except sr.RequestError as e:
                    print(f"Could not request results from Google Speech Recognition service; {e}")
                    self.user_message = self.user_message + f"Could not request results from Google Speech Recognition service; {e} \n"
                    self.label_log.setText(self.user_message)
                    word_count.append(0)
                    timestamps.append([])
                    
        # celalalt caz comentarii si cod similare, trebuie modificat doar filepath-ul 
        elif(aux == 2) :
            for i in range(0,total_segments-1):
                file_path = f"T_Batches/T_segment_{i+1}"+ "__" + audio_id + ".wav"
                segment_timestamps = []
                segment_word_count = 0
                info = sf.info(file_path) 
                segment_duration_seconds = info.duration  # Total duration of the audio file in seconds
            
                with sr.AudioFile(file_path) as source:
                    audio_data = recognizer.record(source)
                    try:
                        text = recognizer.recognize_google(audio_data, language="ro-RO")  # Recognize speech in Romanian
                        text_words = text.lower().split()
                        
                        for word in text_words:
                            if word in target_words:
                                segment_word_count += 1
                        segment_timestamps = self.get_timestamp(file_path,segment_word_count)
                        timestamps.append(segment_timestamps)
                        word_count.append(segment_word_count)
                    except sr.UnknownValueError:
                        print(f"Speech recognition could not understand the audio in the tranzition segment {i+1} ")
                        self.user_message = self.user_message  + (f"Speech recognition could not understand the audio in the tranzition segment {i+1} \n")
                        self.label_log.setText(self.user_message)
                        word_count.append(0)
                        timestamps.append([])
                    except sr.RequestError as e:
                        print (f"Could not request results from Google Speech Recognition service; {e}")
                        self.user_message = self.user_message + (f"Could not request results from Google Speech Recognition service; {e} \n")
                        self.label_log.setText(self.user_message)
                        word_count.append(0)
                        timestamps.append([])
        return word_count, timestamps
        
    ###################################################################
    ### Functia de procesare, care apeleaza toate celalalte functii ###
    ###################################################################
    
    def process(self, audio_id):
        
        # timpul cand am inceput procesarea
        start_time = time.time()
        
        info = sf.info(audio_id + " recorded_audio.wav")
        audio_length_seconds = info.duration
        # determinam numarul total de segmente
        total_segments = self.batch(audio_id)

        # creeam segmente de tranzitie
        self.transition_segment(audio_id,total_segments)

        # determinam listele de aparitii si de momente de timp pentru segmentele de tranzitie si segmentele normale
        word_count_segments, timestamps_segments = self.count_word_and_timestamps(audio_id,self.target_words,total_segments,1)
        word_count_T_segments, timestamps_T_segments = self.count_word_and_timestamps(audio_id,self.target_words,total_segments,2)

        # parcurgem toate segmentele de tranzitie
        i=0
        while i < len(word_count_T_segments):
            # daca avem cuvinte tinta in segmentul de tranzitie 
            if(word_count_T_segments[i]!=0):
               # cenzuram segmentul de tranzitie
               self.censor(audio_id,i,timestamps_T_segments[i],1) 
               # cenzuram si segmentul corespunzator (cel de dinainte de elementul detranzitie)
               self.censor(audio_id,i,timestamps_segments[i],0)
                
               file_path = f"Censored/segment_{i+1}"+ "__" + audio_id + ".wav"
               with wave.open(file_path, 'rb') as wav_file:
                   num_frames = wav_file.getnframes()
                   frame_rate = wav_file.getframerate()
                   duration = num_frames / float(frame_rate)
                # daca dureaza mai mult de o secunde pentru ca atat taiem din el
               if(duration > 1):
                    self.crop(audio_id, i,"first") # pentru ca este primul de cropat
               
               # trecem la urmatorul segment
               i = i + 1
               # il cenzuram si pe acela
               self.censor(audio_id,i,timestamps_segments[i],0)
               
               file_path = f"Censored/segment_{i+1}"+ "__" + audio_id + ".wav"
               with wave.open(file_path, 'rb') as wav_file:
                   num_frames = wav_file.getnframes()
                   frame_rate = wav_file.getframerate()
                   duration = num_frames / float(frame_rate)
                   # daca are si lungimea din care putem sa taiem il taiem
                   if(duration > 1):
                       self.crop(audio_id, i,"last")  # pentru ca este al doilea de cropat
                   i = i + 1 
            else:
                # Daca nu avem cuvinte tinta in partea de tranzitie, verificam daca avem de cenzurat, daca nu :
                if(word_count_segments[i] == 0 ):
                      file_path_source = f"Batches/segment_{i+1}"+ "__" + audio_id + ".wav"
                      file_path_destination = f"Censored/segment_{i+1}"+ "__" + audio_id + ".wav"
                      # fisierul e conform, deci trebuie doar mutat dintr-o parte in alta
                      shutil.move( file_path_source, file_path_destination)
                      i = i + 1
                else :
                    # altfel cenzuram segmentul
                    self.censor(audio_id,i,timestamps_segments[i],0)
                    i = i + 1
        # lucrand asa prelucram perechi de segmente si segmente tranzitie, deci ultimul ramane singur
        
        # trebuie prelucrat si ultimul segment:
        # daca ultimul element e 
        if( word_count_segments[-1] == 0):
            file_path_source = f"Batches/segment_{i+1}"+ "__" + audio_id + ".wav" 
            file_path_destination = f"Censored/segment_{i+1}"+ "__" + audio_id + ".wav"
            #doar il mutam dintr-o parte in alta
            shutil.move( file_path_source, file_path_destination)
        #altfel
        else:
            self.censor(audio_id,i,timestamps_segments[i],0)

        # construim fisierul cenzurat, din toate segmentele .wav cenzurate
        self.build_wav(audio_id)

        ### Mesaje pentru debug
        print(f"Word count segmente : {word_count_segments}")
        self.user_message = self.user_message + (f"Word count segmente : {word_count_segments} \n")
        
        print(f"Time stamp segmente : {timestamps_segments}")
        self.user_message = self.user_message + (f"Time stamp segmente : {timestamps_segments}\n")

        print(f"Word count T_segmente : {word_count_T_segments}")
        self.user_message = self.user_message + (f"Word count T_segmente : {word_count_T_segments}\n")
        
        print(f"Time stamp T_segmente : {timestamps_T_segments}")
        self.user_message =  self.user_message + (f"Time stamp T_segmente : {timestamps_T_segments}\n")

        # timpul cand s-a terminat procesarea
        stop_time = time.time()

        # calculam timpul trecut
        elapsed_time = stop_time - start_time
        # rotunjim
        elapsed_time = round(elapsed_time,2)
        # Acutalizam mesajul pentru utilizator
        self.user_message = self.user_message + (f"Timul de prelucrare a fost :  {elapsed_time}")
    
    # Functiile de start stop inregistrare
    def record(self):
        self.do_record = True
        # Dezactivarea butonului de record si activarea celui de stop
        self.button_record.setEnabled(False)
        self.button_stop_recording.setEnabled(True)
        self.Start()

        # functie care asigura ca se inregistreaza atata timp cat butonul de record este apasat
        def audio_callback(indata, frames, time, status):
            if self.do_record:
                self.audio_data.append(indata.copy())
               
                
        with sd.InputStream(callback=audio_callback):
            while self.do_record:
                QApplication.processEvents()

        # la iesirea din functie oprim inregistrarea modificam starea butoanelor
        self.button_record.setEnabled(True)
        self.button_stop_recording.setEnabled(False)
        
        
        
    def stop_recording(self):
        self.Re_set()
        self.do_record = False
        if self.audio_data:
            # obtinem identificatorul unic
            current_datetime = datetime.now()
            current_datetime_str = current_datetime.strftime("%y%m%d_%H%M%S")
            audio_id =  current_datetime_str
            audio_name = audio_id + " recorded_audio.wav"
            # scriem fisierul inregistrat cu sample-rateul de 44100 si o sa fie salvat pe 24 de biti
            sf.write(audio_name, np.vstack(self.audio_data), 44100, 'PCM_24')
        self.audio_data = []

        ### determinam graficul semnalului nostru audio
        spf = wave.open(audio_name, "r")
        frame_rate = spf.getframerate()
        signal = spf.readframes(-1)
        signal = np.frombuffer(signal, dtype=np.int16)
        
        plt.figure(1)
        plt.title("Signal Wave")
        plt.plot(signal)
        plt.xlabel("Sample")
        plt.ylabel("Amplitude")
        plt.savefig("plot_semnal_audio.png")
        
        # Atribuim graficul elementului corespunzator in interfata si il stergem din sistem dupa
        pixmap = QPixmap("plot_semnal_audio.png")
        os.remove("plot_semnal_audio.png")
        
        # Afisam graficul
        self.label_plot.setPixmap(pixmap)
        # Apelam functia de procesare
        self.process(audio_id)
        # Resetam user message in caz ca se incearca aplicatia de mai multe ori fara a iesi din ea, ploturile o sa se suprascire
        self.user_message = ""


In [ ]:
# Cod principal, din laboratorul 1
if __name__ == "__main__" :
    
    # Crearea unei aplicatii in PyQt5
    App = QApplication(sys.argv)
    
    # Crearea unei instante a clasei definite mai sus
    window = MainWindow()
    
    # Executarea aplicatiei, afisarea ferestrei
    App.exec_() 
    
    # Terminarea aplicatiei atunci cand este apasat butonul X
    App.quit() 
    
# Resetarea tuturor variabilelor create pentru a evita conflictele la rularea multipla
%reset -f

240529_172456 recorded_audio.wav
Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%
Count iter : 1
Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%
Count iter : 2
Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%
Count iter : 3
Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%
Count iter : 4
Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%
Count iter : 5
Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%
Count iter : 6
Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%
Count iter : 7
Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%
Count iter : 8
Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%
Count iter : 9
Caz si mai nefericit ca avem mai multe cuvinte suspecte :  scadem pasul cu 0.5%
Count iter : 10
Caz si mai nefer